In [ ]:
from matplotlib import pyplot as plt
import numpy as np
from qutip import *
import numpy as np
import matplotlib.transforms as transforms
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

from scipy import signal

# Lecture 1: Noise in measurements

```{admonition} Expected prior knowledge
:class: tip
Before the start of this lecture, you should be able to:

- recall the definition of a Fourier transform 
```

```{admonition} Learning goals
:class: important
After this lecture you will be able to:

- estimate average quantities and their statistical error from noisy measurements
- characterize noise via its power spectral density
- identify common kinds of noise spectra
```   

Consider the following problem. We have a small voltage that we want
to measure. We assume the voltage to be constant in time. To measure it, we connect the small voltage to an amplifier and then
connect our amplified signal to an oscilloscope that records the voltage at its
input as a function of time. 

[<div align="center"><img src="figures/1/scope.PNG" width="500"/></div>](scope.png)

On our oscilloscope screen, we see the following trace:

In [ ]:
mu, sigma = 0, 1
ts = np.linspace(0,100,100)
vs = np.asarray([np.random.normal(mu,sigma) for t in ts])

plt.plot(ts, vs)
plt.title("Signal")
plt.xlabel("Time (s)")
plt.ylim(-3,3)
plt.ylabel("Voltage (mV)")
plt.show()

What is approximately the value of the voltage?
- the average of the trace seems to be about 0 mV
- How can we quantify how close it is to 0 mV?

A good first step: create a histogram of the data, which might look like

In [ ]:
count, bins, ignored = plt.hist(vs, 20, density=True)
plt.plot(bins, 1/(sigma * np.sqrt(2 * np.pi)) * np.exp( - (bins - mu)**2 / (2 * sigma**2) ),
         linewidth=2, color='r')
plt.title("Histogram of measured voltages and fit to a Gaussian probability distribution")
plt.xlabel("Voltage [mV]")
plt.ylabel("Probability of voltage value")
plt.show()

(In this histogram, we have normalized the bin counts to match the Gaussian fit.)

Fitting to a Gaussian, we find a full-width half-maximum (FWHM) of 2 mV. We thus estimate that, on average, the statistical error in each measurement point is about $\pm 1$ mV.

However, because we assumed that the voltage we are trying to measure is constant in time, we can reduce the error in our estimate of the 
unknown small voltage by averaging points together. We know how to calculate the average, but what is the uncertainty in this average value? 

```{admonition} Standard error of the mean
:class: note
The error $\sigma_N$ of our average of $N$ points is related to the error $\sigma_1$ of a single point by 

$$
\sigma_N^2 = \frac{\sigma_1^2}{N}
$$

The quantity $\sigma_N$ is known as the standard error of the mean. How is this quantity related to our histogram above? Adding
more points will not change the *shape* of the distribution, it will only give 
more counts in each bin. 
```

The reduction of $\sigma_N$ with respect to $\sigma_1$, however, has nothing to do with the width of the histogram. Rather, it determines how accurately we can determine the center of the peak (the average): The more points we add, the smaller the (relative) statistical fluctuations in the height of each bin will become, and the more accurately we will be able to find the center of the peak.

```{admonition} Caveat
:class: warning
The above equation relating the standard error of the mean $\sigma_N$ to the standard error of a single measurement $\sigma_1$ is only true if the noise in your data is *uncorrelated*, which means that each data point in your trace represents an independent sampling of the random noise of your amplifier. 
```

```{admonition} Autocorrelation function
:class: note
How can one know if the noise is uncorrelated? By calculating its autocorrelation function. For a function $v(t)$ it is defined as

$$
R_{vv}(\tau) =  \langle v(t+\tau) v(t) \rangle
$$

where the angled brackets denote the expectation value/ensemble average.
```

A common example of correlated noise arises when your signal has some "memory" that is slower than your sampling rate such that consecutive samples will have similar values.  For example, if you put a 1 kHz low-pass
filter after your amplifier, but configure your oscilloscope to record the signal
with a 10 kHz sampling rate, then $R_{vv}$ will look something like this:

In [ ]:
ts = np.linspace(0,3,31)
ys = np.exp(-ts)
plt.plot(ts, ys)
plt.title("Autocorrelation function")
plt.ylabel("$R_{vv}$")
plt.xlabel("Time difference between data points (ms)")
plt.show()

In this example, we can see that each measured value displayed on our oscilloscope will be strongly correlated with several values in its direct neighborhood. In this case, the values are not independently drawn from the random distribution, and the error in our estimate of the average voltage will *not* scale with $\frac{1}{N}$ if we average $N$ such points

## Power Spectral Density

To summarize so far:

- The error in estimating the average of a noisy measurement depends on how many (uncorrelated) points we measure
- If we record a dataset of uncorrelated points for a time $T_m$, the error in our estimate of the mean value will go down as $\sigma_T^2 \propto \frac{1}{T_m}$

However, if we measure for longer periods of time, then our measurements are
slower. This becomes an issue if we want to measure a signal that is not constant in time, because increasing $T_m$ reduces
the speed at which we can record a changing signal.  Thus, there is a tradeoff
between the noise level $\sigma_v$ and the *bandwidth* of your measurement.

```{admonition} Question
:class: question
if you want buy an amplifier, does it make sense to look at its noise level without looking at its bandwidth? Why (not)?
```

So then, how do we characterize noisy, time-varying signals? We can compute
the power spectral density $S_{xx}(\omega)$, which tells us how the "noise
power" is distributed across different frequencies.

```{admonition} Definitions
:class: discussion
1. For a signal $V(t)$, we first define a (finite-time, truncated) Fourier 
transform:

$$
\hat{V}(\omega) = \frac{1}{\sqrt{T}} \int_0^T V(t)e^{-i \omega t} dt
$$

where the prefactor $\frac{1}{\sqrt{T}}$ is for normalization.

2. The power spectral density is then defined as the "ensemble average" of the magnitude
of $\hat{V}(\omega)$:

$$
S_{VV}(\omega) = \big \langle | \hat{V}(\omega) |^2 \big \rangle
$$

3. What do we mean by "ensemble average"?

- If the noise in our measurement is random, its Fourier transform is also 
random
- To reduce the "noise" in our estimate of the noise, we average over the 
$|\hat{V}(\omega)|^2$ of many different measurement traces

The power spectral density describes how the power in a signal is distributed over different frequencies. It is also called the power spectrum. 
```

How could we measure a power spectral density in practice?

[<div align="center"><img src="figures/1/filter.PNG" width="500"/></div>](filter.png)

Here, the bandpass filter transmits the part of the signal within a frequency band $\Delta \omega$ centered at $\omega_0$. The rectifier converts the transmitted signal into a DC voltage $V_\text{out}$. As a result, $V_\text{out}$ is proportional to the amount of power present in $v(t)$ in the frequency band $\omega_0\pm\Delta\omega/2$, given by $ V_{out}^2 = S_\text{vv}(\omega_0) {\Delta \omega} $

## Types of noise specta

### White noise
Uncorrelated noise is called 'white noise'. Its power spectral density is flat (independent of frequency)

In [ ]:
fs = 1e3
N = 1e5
amp = 2*np.sqrt(2)
freq = 1234.0
noise_power = 0.001 * fs / 2
time = np.arange(N) / fs
x = 0
# x = amp*np.sin(2*np.pi*freq*time)
x += np.random.normal(scale=np.sqrt(noise_power), size=time.shape)

f, Pxx_den = signal.welch(x, fs, nperseg=len(x)//4)
plt.semilogy(f, Pxx_den)
plt.ylim([1e-7, 1e2])
plt.title("White Noise")
plt.xlabel('frequency [Hz]')
plt.ylabel('PSD [V**2/Hz]')
plt.show()

### 1/f noise
Common in many experiments, particularly for f < 100kHz

In [ ]:
plt.semilogy(f[1:], Pxx_den[1:]/f[1:])
#plt.ylim([1e-7, 1e2])
plt.xlim([0,200])
plt.title("1/f Noise (also called 'pink' noise)")
plt.xlabel('frequency [Hz]')
plt.ylabel('PSD [V**2/Hz]')
plt.show()

In [ ]:
plt.semilogy(f[1:], Pxx_den[1:]/f[1:])
#plt.ylim([1e-7, 1e2])
plt.xlim([0,200])
plt.title("1/f Noise (also called 'pink' noise)")
plt.xlabel('frequency [Hz]')
plt.ylabel('PSD [V**2/Hz]')
plt.show()

### "Peaked" noise

In [ ]:
plt.semilogy(f, Pxx_den/(1+(f-100)**2))
plt.ylim([1e-8, 1e-2])
plt.xlim([0,200])
plt.title("Peaked noise")
plt.xlabel('frequency [Hz]')
plt.ylabel('PSD [V**2/Hz]')
plt.show()

```{admonition} Calculating the noise in a measurement from a known power spectral density
:class: example
Suppose the spec sheet of our amplifier specifies $S_\text{vv}=1 \, \text{nV}^2/\text{Hz}$ within the amplifier bandwidth (0-1 MHz). We can then calculate the expected fluctuations $\sigma_v$ of the data points in a timetrace $V(t)$ that we would measure with an oscilloscope, using

$$
\sigma_v^2 = \int_{\omega_1}^{\omega_2} S_\text{vv}(\omega) d\omega
$$

What determines $\omega_1$ and $\omega_2$? If we measure for a total time $T_m$, we are insensitive to frequencies below $\omega_1 = 1/T_m$. Furthermore, $\omega_2$ is given by the upper limit of the bandwidth of our amplifier (1 MHz), assuming that our oscilloscope does not limit the measurement bandwidth. If $T_m= 1$ s, then 

$$
\begin{align}
\sigma_\text{v}^{2} &= \int_{1}^{10^6} \frac{1 \, \text{nV}^2}{\text{Hz}} df\\
&= 10^{-18} (10^6 - 1) \approx 10^{-12} \, \text{V}^2\\
\sigma_\text{v} &= 1 \, \mu\text{V}
\end{align}
$$

so the RMS noise on the measurement will be 1$\mu $V

What if we put a 1 kHZ low-pass filter on the output of our amplifier?

$$ 
\begin{align}
\sigma_\text{v}^{2} &= \int_{1}^{10^3} \frac{1 \, \text{nV}^2}{\text{Hz}} df \\
= & 10^{-15} \, \text{V}^2\\
\sigma_\text{v} &= 31 \, \text{nV}
\end{align}
$$
```

```{admonition} Conclusions
:class: important
1. Measuring longer decreases the uncertainty in the average of the measured quantity according to $\sigma_N^2= \sigma_1^2/N $, provided the N data points are uncorrelated.
2. The power spectral density $S_{xx}(\omega)$ is the Fourier transform of the autocorrelation function $R_{xx}(t)$:

$$
S_{xx}(\omega) = \int_{-\infty}^{+\infty} R_{xx}(t) e^{-i\omega t} dt
$$

3. For uncorrelated noise, $R_{xx}(\tau) = \delta(\tau)$, such that $S_{xx}(\omega)$ is a constant (white noise)
4. The expected noise in a data trace can be calculated by integrating over the power spectral density
```

### Demonstration: Noise after averaging 


In [ ]:
# Increase the animation embed limit
plt.rcParams['animation.embed_limit'] = 60

# Start with Gaussian noise
N = 10000
x = np.random.normal(size=N)

Navg = np.geomspace(1, N / 20, 100).astype(int) # 100 points between 1 and N/20
Navg = np.unique(Navg) # remove duplicates

def average_points(x, n):
    n_out = len(x) // n
    # A trick for using reshape
    x = x[0:n * n_out]
    x = np.reshape(x, [n, n_out])
    return np.average(x, axis=0)

averages = []
sigma = np.zeros(len(Navg))
# calculates the averages for different values of n and stores them in the averages list.
# also calculates the standard deviation of these averages and stores them in the sigma array
for i in range(len(Navg)):
    averages.append(average_points(x, Navg[i]))
    sigma[i] = np.std(averages[i])

i = 0
N = 2000
c = 'orange'

fig, (ax1, ax2) = plt.subplots(2, 1, figsize=(16, 12), dpi=200)
ax1.set_xscale('log')
ax1.set_yscale('log')
ax1.set_title("N_avg = %d" % Navg[i])
l1, = ax1.plot(Navg, sigma)
cir1 = ax1.scatter(Navg, sigma)
cir2 = ax1.scatter(Navg[i:i+1], sigma[i:i+1], color=c)

l2, = ax2.plot(range(N), x[0:N])
cir3 = ax2.scatter(range(N), x[0:N])
xax = np.linspace(0, N, N // Navg[i])
yax = averages[i][0:N // Navg[i]]
l3, = ax2.plot(xax, yax, color=c)
cir4 = ax2.scatter(xax, yax, color=c, facecolors='none')

def update_plot(i):
    n = Navg[i] # Navg[i] is the number of points to average
    ax1.set_title("N_avg = %d" % n)
    cir2.set_offsets(np.column_stack((Navg[i:i+1], sigma[i:i+1])))
    xax = np.linspace(0, N, N // n)
    yax = averages[i][0:N // n]
    l3.set_data(xax, yax)
    cir4.set_offsets(np.column_stack((xax, yax)))

frames = range(len(Navg)) # include all frames
ani = FuncAnimation(fig, update_plot, frames=frames)

plt.close(fig)
# show the animation
HTML(ani.to_jshtml())

### Demonstration: "Ensemble averaging" PSD (reducing the noise of the noise...)


In [ ]:
# Increase the animation embed limit
plt.rcParams['animation.embed_limit'] = 60

# Number of points in an individual data trace
N = 1000

# Number of "ensemble" members to make
M = 500

v = np.random.normal(size=(N, M))

# Take the Fourier transform
vt = np.fft.fft(v, axis=0)
f = np.fft.fftfreq(len(v))

# Make our noise spectrum "peaky" so it looks a bit interesting
f0 = max(f) / 3
Q = 10
delta = f - f0
filt = f0 ** 2 / (f0 ** 2 - f ** 2 + 1j * f * f0 / Q)
vt2 = np.zeros(vt.shape) + 0j
for i in range(vt2.shape[1]):
    vt2[:, i] = vt[:, i] * filt

# Create the figure and axes
fig, ax = plt.subplots(figsize=(8, 6) , dpi=150)
line1, = ax.plot(f[:N // 3], np.abs(vt2[:N // 3, 0]), color='blue', lw=1)
line2, = ax.plot(f[:N // 3], np.abs(vt2[:N // 3, 0]), 'ro', markersize=1.2)


# Set the axis labels and title
ax.set_xlabel('Frequency')
ax.set_ylabel('Amplitude')
ax.set_title('Ensemble Averaging')

# Update function for the animation
def update(frame):
    avg = np.average(np.abs(vt2[:N // 3, :frame + 1]), axis=1)
    line1.set_ydata(avg)
    line2.set_ydata(np.abs(vt2[:N // 3, -1]))
    ax.set_title('Ensemble Averaging, N_avg = %d' % (frame + 1))
    return line1, line2

# Create the animation
animation = FuncAnimation(fig, update, frames=M, interval=200, blit=True)

# Display the animation
plt.close(fig)
HTML(animation.to_jshtml())
